In [9]:
def makePredictions(list_of_text, model):
    from transformers import AutoTokenizer
    tokenizer = AutoTokenizer.from_pretrained("bert-base-cased")
    
    import torch
    device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")
    
    # padding = True vs padding = "max_length"
    sample = tokenizer(list_of_text, padding=True, truncation=True)

    sample['input_ids'] = torch.Tensor(sample['input_ids']).to(torch.int64)
    sample['token_type_ids'] = torch.Tensor(sample['token_type_ids']).to(torch.int64)
    sample['attention_mask'] = torch.Tensor(sample['attention_mask']).to(torch.int64)

    batch = {k: v.to(device) for k, v in sample.items()}
    with torch.no_grad():
        outputs = model(**batch)

    predictions = torch.argmax(outputs.logits, dim=-1)
    return predictions  

In [10]:
def getEmbeddings(text, model, tokenizer):
    
    import torch
    device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")
#     device = torch.device("cpu")
    model.to(device)
    # padding = True vs padding = "max_length"

    sample = tokenizer(text, padding=True, truncation=True)

    sample['input_ids'] = torch.Tensor(sample['input_ids']).to(torch.int64)
    sample['token_type_ids'] = torch.Tensor(sample['token_type_ids']).to(torch.int64)
    sample['attention_mask'] = torch.Tensor(sample['attention_mask']).to(torch.int64)

    batch = {k: v.to(device) for k, v in sample.items()}
    with torch.no_grad():
        outputs = model.bert(**batch)
    
    return outputs.pooler_output

In [11]:
# Function that returns a new dataframe with reduced sentence sizes (as most bert models have a max_seq_length)

def updateDataFrame(csv_file_name, model_max_length=500):
    import pandas as pd
    data = pd.read_csv(csv_file_name)
    data = data.drop(columns=['Unnamed: 0'])
    
    def split_sentences(list_of_words):
        chunked_list = list()
        chunk_size = model_max_length
        for i in range(0, len(list_of_words), chunk_size):
            chunked_list.append(list_of_words[i:i+chunk_size])

        return chunked_list

    for idx in range(len(data['data_string'])):
#         print(data['data_string'][idx])
#         data['data_category_number'][idx] = data['data_category_number'][idx] - 1
        data['data_category_number'][idx] = data['data_category_number'][idx]
        if len(str(data['data_string'][idx]).split()) > 500:
#             print(True)
            tempString = data['data_string'][idx]
            tempStringSplit = tempString.split()
            chunkedLists = split_sentences(tempStringSplit)
        
            for sentence in chunkedLists:
                tempSentence = " ".join(sentence)
                data.loc[len(data.index)] = [
                                            data['data_id'][idx], 
                                             tempSentence,
                                            data['2d_coor'][idx],
                                            data['data_title'][idx],
                                            data['data_category'][idx],
                                            data['data_category_number'][idx],
                                            ]
    return data

In [27]:
def fineTuneModel(df, number_of_labels, number_of_epochs=3):
    from datasets import load_dataset, Dataset
    #     dataset = load_dataset('csv', data_files='Care_Reviews.csv', split='train')
    df = df.dropna()
    print(df)
    df['data_category_number'] = df['data_category_number'].astype(int)
    dataset = Dataset.from_pandas(df)
    dataset = dataset.remove_columns(['__index_level_0__'])

    from datasets import DatasetDict
    
    train_testvalid = dataset.train_test_split()
    test_valid = train_testvalid['test'].train_test_split()
    
    train_test_valid_dataset = DatasetDict({
    'train': train_testvalid['train'],
    'test': test_valid['test'],
    'valid': test_valid['train']})
    
    dataset = train_test_valid_dataset.remove_columns(['data_id', '2d_coor', 'data_title','data_category'])
    print(dataset)
    from transformers import AutoTokenizer

    tokenizer = AutoTokenizer.from_pretrained("bert-base-cased")


    def tokenize_function(examples):
    # refer documentation: padding=True or padding="max_length"
        return tokenizer(examples["data_string"], padding=True, truncation=True)

    tokenized_datasets = dataset.map(tokenize_function, batched=True)

    train_dataset = tokenized_datasets["train"]
    eval_dataset = tokenized_datasets["valid"]
    test_dataset = tokenized_datasets['test']

    tokenized_datasets = tokenized_datasets.remove_columns(["data_string"])
    
#     tokenized_datasets = tokenized_datasets.remove_columns(["data_string"])
    tokenized_datasets = tokenized_datasets.rename_column("data_category_number", "labels")
    
    tokenized_datasets.set_format("torch")
    
    small_train_dataset = tokenized_datasets["train"]
    small_eval_dataset = tokenized_datasets["test"]
    print(small_train_dataset)
    
    from torch.utils.data import DataLoader
    train_dataloader = DataLoader(small_train_dataset, shuffle=True, batch_size=8)
    eval_dataloader = DataLoader(small_eval_dataset, batch_size=8)
    
    from transformers import AutoModelForSequenceClassification
    model = AutoModelForSequenceClassification.from_pretrained("bert-base-cased", num_labels=number_of_labels)
    
    from torch.optim import AdamW
    optimizer = AdamW(model.parameters(), lr=5e-5)
    
    from transformers import get_scheduler

    num_epochs = number_of_epochs
    num_training_steps = num_epochs * len(train_dataloader)
    lr_scheduler = get_scheduler(
        name="linear", optimizer=optimizer, num_warmup_steps=0, num_training_steps=num_training_steps
    )
    
    import torch
    

    device = torch.device("mps") #if torch.cuda.is_available() else torch.device("cpu")
#     device = torch.device("cpu")
    model.to(device)
    
    from tqdm.auto import tqdm
    progress_bar = tqdm(range(num_training_steps))

    model.train()
    for epoch in range(num_epochs):
        for batch in train_dataloader:
            batch = {k: v.to(device) for k, v in batch.items()}
            outputs = model(**batch)
            loss = outputs.loss
            loss.backward()

            optimizer.step()
            lr_scheduler.step()
            optimizer.zero_grad()
            progress_bar.update(1)
#             break
#         break
            
    from datasets import load_metric
    metric = load_metric("accuracy")
    model.eval()
    for batch in eval_dataloader:
        batch = {k: v.to(device) for k, v in batch.items()}
        with torch.no_grad():
            outputs = model(**batch)

        logits = outputs.logits
        predictions = torch.argmax(logits, dim=-1)
        metric.add_batch(predictions=predictions, references=batch["labels"])

    final_score = metric.compute()
    return model, final_score

In [13]:
import torch
print(torch.__version__)
if not torch.backends.mps.is_available():
    if not torch.backends.mps.is_built():
        print("MPS not available because the current PyTorch install was not "
              "built with MPS enabled.")
    else:
        print("MPS not available because the current MacOS version is not 12.3+ "
              "and/or you do not have an MPS-enabled device on this machine.")

1.13.0.dev20220707


In [14]:
def get_json_file(data, model, output_file_name="something.json"):
    from transformers import AutoTokenizer
    tokenizer = AutoTokenizer.from_pretrained("bert-base-cased")
    
    embedding_list = []
    for idx in range(len(data['data_string'])):
        if type(data['data_string'][idx]) is float:
            continue
        embed = getEmbeddings([data['data_string'][idx]], model, tokenizer).tolist()[0]
        embedding_list.append(embed)
    
    import numpy as np
    embeddings_for_umap = np.array(embedding_list)
    
    import umap.umap_ as umap
    umap_embedding = umap.UMAP().fit_transform(embeddings_for_umap, y=list(data['data_category_number']))
    
    data['2d_coor'] = umap_embedding.tolist()
    
    list_of_points = []
    for idx in range(len(data['data_string'])):
        tmp_dict = {}
    #     tmp_var = data_df_china_news['2d_coor'][idx].strip('][').split(', ')
        tmp_dict["data_x"] = str(data['2d_coor'][idx][0])
        tmp_dict["data_y"] = str(data['2d_coor'][idx][1])
    #     tmp_dict["data_x"] = str(tmp_var[0])
    #     tmp_dict["data_y"] = str(tmp_var[1])
        tmp_dict["data_category_number"] = str(data['data_category_number'][idx])
        tmp_dict["data_id"] = str(data['data_id'][idx])
#         tmp_dict["data_string"] = str(data['data_string'][idx])
        tmp_dict["data_title"] = str(data['data_title'][idx])
        tmp_dict["data_category"] = str(data['data_category'][idx])

        list_of_points.append(tmp_dict)
        
    import json
    with open(output_file_name, "w") as outfile:
        json.dump(list_of_points, outfile)
        
    return data

In [15]:
def train_masked_bert(data, num_epochs=2, number_of_labels=5):
    from transformers import AutoTokenizer, BertForMaskedLM
    import torch

    tokenizer = AutoTokenizer.from_pretrained('bert-base-cased')
    model = BertForMaskedLM.from_pretrained('bert-base-cased')
    
    data = data.dropna()
    display(data)
    inputs = tokenizer(list(data['data_string']), return_tensors='pt', padding=True, truncation=True)
    
    inputs['labels'] = inputs.input_ids.detach().clone()
    
    # create random array of floats with equal dimensions to input_ids tensor
    rand = torch.rand(inputs.input_ids.shape)
    # create mask array
    mask_arr = (rand < 0.15) * (inputs.input_ids != 101) * \
           (inputs.input_ids != 102) * (inputs.input_ids != 0)
    
    selection = []

    for i in range(inputs.input_ids.shape[0]):
        selection.append(
            torch.flatten(mask_arr[i].nonzero()).tolist()
        )
    
    for i in range(inputs.input_ids.shape[0]):
        inputs.input_ids[i, selection[i]] = 103
        
    class CustomDataset(torch.utils.data.Dataset):
        def __init__(self, encodings):
            self.encodings = encodings
        def __getitem__(self, idx):
            return {key: torch.tensor(val[idx]) for key, val in self.encodings.items()}
        def __len__(self):
            return len(self.encodings.input_ids)
        
    dataset = CustomDataset(inputs)
    
    loader = torch.utils.data.DataLoader(dataset, batch_size=4, shuffle=True)
    
    device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
    # device = torch.device('cpu')
    # and move our model over to the selected device
    model.to(device)
    # activate training mode
    model.train()
    
    from transformers import AdamW
    # initialize optimizer
    optim = AdamW(model.parameters(), lr=5e-5)
    
    from tqdm import tqdm  # for our progress bar

    epochs = num_epochs

    for epoch in range(epochs):
        # setup loop with TQDM and dataloader
        loop = tqdm(loader, leave=True)
        for batch in loop:
            # initialize calculated gradients (from prev step)
            optim.zero_grad()
            # pull all tensor batches required for training
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_mask'].to(device)
            labels = batch['labels'].to(device)
            # process
            outputs = model(input_ids, attention_mask=attention_mask,
                            labels=labels)
            # extract loss
            loss = outputs.loss
            # calculate loss for every parameter that needs grad update
            loss.backward()
            # update parameters
            optim.step()
            # print relevant info to progress bar
            loop.set_description(f'Epoch {epoch}')
            loop.set_postfix(loss=loss.item())
            torch.cuda.empty_cache()
#             break
#         break
            
    model.save_pretrained('pytorch_model_unsupervised_finetuned')
    return None

In [16]:
def fineTuneModelUnsupervised(df, number_of_labels=19, number_of_epochs=3):
    from datasets import load_dataset, Dataset
    #     dataset = load_dataset('csv', data_files='Care_Reviews.csv', split='train')
    df = df.dropna()
    display(df)
    dataset = Dataset.from_pandas(df)
    #dataset = dataset.remove_columns(['__index_level_0__'])

    from datasets import DatasetDict
    
    train_testvalid = dataset.train_test_split()
    test_valid = train_testvalid['test'].train_test_split()
    
    train_test_valid_dataset = DatasetDict({
    'train': train_testvalid['train'],
    'test': test_valid['test'],
    'valid': test_valid['train']})
    
    dataset = train_test_valid_dataset.remove_columns(['data_id', '2d_coor', 'data_title','data_category'])
    
    from transformers import AutoTokenizer

    tokenizer = AutoTokenizer.from_pretrained("bert-base-cased")


    def tokenize_function(examples):
    # refer documentation: padding=True or padding="max_length"
        return tokenizer(examples["data_string"], padding=True, truncation=True)

    tokenized_datasets = dataset.map(tokenize_function, batched=True)

    train_dataset = tokenized_datasets["train"]
    eval_dataset = tokenized_datasets["valid"]
    test_dataset = tokenized_datasets['test']

    tokenized_datasets = tokenized_datasets.remove_columns(["data_string"])
    
#     tokenized_datasets = tokenized_datasets.remove_columns(["data_string"])
    tokenized_datasets = tokenized_datasets.rename_column("data_category_number", "labels")
    
    tokenized_datasets.set_format("torch")
    
    small_train_dataset = tokenized_datasets["train"]
    small_eval_dataset = tokenized_datasets["test"]
#     print(small_eval_dataset)
    
    from torch.utils.data import DataLoader
    train_dataloader = DataLoader(small_train_dataset, shuffle=True, batch_size=8)
    eval_dataloader = DataLoader(small_eval_dataset, batch_size=8)
    
    from transformers import AutoModelForSequenceClassification
    model = AutoModelForSequenceClassification.from_pretrained("pytorch_model_unsupervised_finetuned", num_labels=number_of_labels)
    
    from torch.optim import AdamW
    optimizer = AdamW(model.parameters(), lr=5e-5)
    
    from transformers import get_scheduler

    num_epochs = number_of_epochs
    num_training_steps = num_epochs * len(train_dataloader)
    lr_scheduler = get_scheduler(
        name="linear", optimizer=optimizer, num_warmup_steps=0, num_training_steps=num_training_steps
    )
    
    import torch

    device = torch.device("cuda") if torch.cuda.is_available() else torch.device("cpu")
    model.to(device)
    
    from tqdm.auto import tqdm
    progress_bar = tqdm(range(num_training_steps))

    model.train()
    for epoch in range(num_epochs):
        for batch in train_dataloader:
            batch = {k: v.to(device) for k, v in batch.items()}
            outputs = model(**batch)
#             print(outputs)
            loss = outputs.loss
            loss.backward()

            optimizer.step()
            lr_scheduler.step()
            optimizer.zero_grad()
            progress_bar.update(1)
#             break
#         break
            
    from datasets import load_metric
    metric = load_metric("accuracy")
    model.eval()
    for batch in eval_dataloader:
        batch = {k: v.to(device) for k, v in batch.items()}
        with torch.no_grad():
            outputs = model(**batch)

        logits = outputs.logits
        predictions = torch.argmax(logits, dim=-1)
        metric.add_batch(predictions=predictions, references=batch["labels"])

    final_score = metric.compute()
    return model, final_score

In [8]:
# Below are functions to delete files and directories (you will not be able to delete directories/files
# directly from the Jupyter Notebook UI)

In [9]:
# use the space below to play (call) with functions initialized above

In [19]:
import pandas as pd
pd.set_option('display.max_columns', None)

data = pd.read_json('news_50k.json')
display(data)


data = data.rename(columns={2:'data_title', 5:'data_string',0:'data_id'})
data
data = data.drop(columns=[1,3,4,6])
data
data['2d_coor'] = ''
data['data_category'] = ''
data['data_category_number'] = ''
data = data.reindex(columns=['data_id', 'data_string', '2d_coor', 'data_title', 'data_category', 'data_category_number'])
data.dropna()
display(data)
data.to_csv('news_50k_test.csv')

0 1                                                   2  \
0         115          The History of Gowanus Cemented in Sculpture   
1         118     Emergency Services Rush to Save Expensive Wine...   
2         119     An Artist Serves Up Food for Thought About Exc...   
3         122     Snap stock took a beating Monday and fell more...   
4         125      Vox Sentences: There’s a coup underway in Turkey   
...       ... ..                                                ...   
21895  239646     BRIEF-Malmbergs Elektriska Q2 operating profit...   
21896  239657     Pitch Invader Kisses the Feet of Messi, Will N...   
21897  239658     The NFL Wants Players to Stay Away from Mexica...   
21898  239531     ​Europe Is Building a ‘Space Data Highway’ Wit...   
21899  240887     A Brief Look at Cutty Bangs: San Francisco's W...   

                                  3           4  \
0                 [Benjamin Sutton]  2016-10-14   
1                  [Hilary Pollack]  2017-09-08   
2      [Devon Van Houten Maldonado]  2017-06-05   
3                     [Kurt Wagner]  2017-03-06   
4                       [Dara Lind]  2016-07-16   
...                             ...         ...   
21895                            []  2016-08-24   
21896          [Liam Daniel Pierce]  2017-09-28   
21897                   [Nick Rose]  2016-05-08   
21898               [Victoria Turk]  2016-01-29   
21899              [Hilary Pollack]  2016-12-28   

                                                       5 6   
0      A collaboration between artist Christina Kelly...     
1      As Hurricane Irma draws closer to the Florida ...     
2      Raúl Ortega Ayala’s new exhibition at Proyecto...     
3      Welcome to the public markets, Snapchat. Stock...     
4      Vox Sentences is written by Dylan Matthews and...     
...                                                  ... ..  
21895  Aug 24 (Reuters) - Malmbergs Elektriska publ A...     
21896  Dearest Lionel Messi, the only way us lowly mo...     
21897  Protein is crucial part of any athlete's diet....     
21898  The first satellite of the European Data Relay...     
21899  As with most American cities, San Francisco ha...     

[21900 rows x 7 columns]

data_id                                        data_string 2d_coor  \
0          115  A collaboration between artist Christina Kelly...           
1          118  As Hurricane Irma draws closer to the Florida ...           
2          119  Raúl Ortega Ayala’s new exhibition at Proyecto...           
3          122  Welcome to the public markets, Snapchat. Stock...           
4          125  Vox Sentences is written by Dylan Matthews and...           
...        ...                                                ...     ...   
21895   239646  Aug 24 (Reuters) - Malmbergs Elektriska publ A...           
21896   239657  Dearest Lionel Messi, the only way us lowly mo...           
21897   239658  Protein is crucial part of any athlete's diet....           
21898   239531  The first satellite of the European Data Relay...           
21899   240887  As with most American cities, San Francisco ha...           

                                              data_title data_category  \
0           The History of Gowanus Cemented in Sculpture                 
1      Emergency Services Rush to Save Expensive Wine...                 
2      An Artist Serves Up Food for Thought About Exc...                 
3      Snap stock took a beating Monday and fell more...                 
4       Vox Sentences: There’s a coup underway in Turkey                 
...                                                  ...           ...   
21895  BRIEF-Malmbergs Elektriska Q2 operating profit...                 
21896  Pitch Invader Kisses the Feet of Messi, Will N...                 
21897  The NFL Wants Players to Stay Away from Mexica...                 
21898  ​Europe Is Building a ‘Space Data Highway’ Wit...                 
21899  A Brief Look at Cutty Bangs: San Francisco's W...                 

      data_category_number  
0                           
1                           
2                           
3                           
4                           
...                    ...  
21895                       
21896                       
21897                       
21898                       
21899                       

[21900 rows x 6 columns]

In [20]:
### Step 1 ###

# This function will create a csv in a format (mostly changing columns names) that we need for training models
# The following columns are needed: data_category_number, data_title, data_string, data_category, data_id, 2d_coor

# Note: This function will have to be modified according to the need as not all datasets have labels but above
# mentioned columns should be there
def create_structured_csv(csv_file_name):
    import pandas as pd
    data = pd.read_csv(csv_file_name)
    #data = data.drop(columns=['Unnamed: 0', 'year'])
    data = data.rename(columns={'seq':'data_category_number', 'title':'data_title', 'abstract':'data_string', 'CODE':'data_category','id':'data_id'})
    data['2d_coor'] = ''
    data = data.reindex(columns=['data_id', 'data_string', '2d_coor', 'data_title', 'data_category', 'data_category_number'])
    data.to_csv('news_50k_cleaned.csv')
    return data

csv_file_name = 'news_50k_test.csv'
data = create_structured_csv(csv_file_name)

In [21]:
### Step 2 ###

# Not all the datasets at DSC are labelled. Hence, we need to label some and we use LDA for that
def apply_lda_on_dataset(df):
    import gensim
    from gensim.utils import simple_preprocess
    from gensim.parsing.preprocessing import STOPWORDS
#     from nltk.stem.porter import *
    from gensim import corpora, models
    import numpy as np
    import pandas as pd
    np.random.seed(2018)

    import nltk
    nltk.download('wordnet')

    # Function that preprocesses all text documents before feeding to lda model
    def preprocess(text):
        result = []
        i = 0
        for token in gensim.utils.simple_preprocess(text):
            if token not in gensim.parsing.preprocessing.STOPWORDS and len(token) > 3:
                result.append(token)
        return result
    
    # the file name should be the one generated from the function above     
#     data = pd.read_csv('Care_Reviews.csv')
    data = df
    documents = data
    documents = documents.dropna(subset=['data_string'])
    processed_docs = documents['data_string'].map(preprocess)
    
    # Creates a dictionary from the documents (Note: Here the argument 'preprocessed_docs' is a 'list of lists')
    dictionary = gensim.corpora.Dictionary(processed_docs)
    
    # Creates a bag_of_words corpus     
    bow_corpus = [dictionary.doc2bow(doc) for doc in processed_docs]

    # Creates a tfidf matrix/table required for training
    tfidf = models.TfidfModel(bow_corpus)
    corpus_tfidf = tfidf[bow_corpus]
    
    # Trains an lda model with tfidf
    lda_model_tfidf = gensim.models.LdaMulticore(corpus_tfidf, num_topics=20, id2word=dictionary, passes=2, workers=4)
    
    for idx in range(len(data['data_string'])):
        data_string = data['data_string'][idx]
#         print(type(data_string))
#         print(dictionary.doc2bow(preprocess(data_string)))
#         print(lda_model_tfidf.get_document_topics())
        data_string_topic_no = lda_model_tfidf.get_document_topics(dictionary.doc2bow(preprocess(data_string)))[0][0]
#         print(data_string_topic_no)
        data_string_topic = lda_model_tfidf.print_topic(data_string_topic_no)
        data['data_category'][idx] = data_string_topic
        data_string_topic_num = lda_model_tfidf.get_document_topics(dictionary.doc2bow(preprocess(data_string)))[0][0]
        data['data_category_number'][idx] = data_string_topic_num
    data['data_category_number'] = data['data_category_number'].astype(int)    
    return data

In [22]:
data = apply_lda_on_dataset(data)

[nltk_data] Downloading package wordnet to /Users/ez/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1938434089.py:54: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category'][idx] = data_string_topic
/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1938434089.py:56: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data_string_topic_num


In [23]:
data.to_csv('news_50k_test_lda.csv')

In [7]:
# The following function is responsible for fine-tuning an existing Bert Model (from huggingface) with a DSC dataset
def finetuneBertSeqModelWithCustomDataset(input_file_name='test_lda.csv', 
                                         model_max_length=500,
                                         number_of_labels=15,
                                         number_of_epochs=15,
                                         output_file_name="something.json"):
    # Function that returns a new dataframe with reduced sentence sizes (as most bert models have a max_seq_length)     
    data = updateDataFrame(input_file_name, model_max_length=model_max_length)
    #data = data.drop(['Unnamed: 0']
    print('Dataframe with reduced sentence sizes: \n')
    display(data)
    # Replacing all NaN fields under '2d_coor' column with an empty string
    print('Dataframe with NaN removed: \n')
    data['2d_coor'] = ''
    #display(data)
    
    # Function that returns a fine-tuned model (fine-tuned on DSC dataset) and its score
    model, score = fineTuneModel(df=data, number_of_labels=number_of_labels, number_of_epochs=number_of_epochs)
    
    print('Here\s the fine-tuned model: ', model)
    print('Accuracy of the fine-tuned model on the test dataset is: ', score)
    
    # Function that returns the dataframe with embeddings (UMAP reduces high dimensional embedding to 2D)     
    data_with_embeddings = get_json_file(data, model, output_file_name)

In [28]:
finetuneBertSeqModelWithCustomDataset(input_file_name='news_50k_test_lda.csv', 
                                         model_max_length=500,
                                         number_of_labels=20,
                                         number_of_epochs=5,
                                         output_file_name="news_50k_test_embs.json")

/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data['data_category_number'][idx]
/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data['data_category_number'][idx]
/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.

/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data['data_category_number'][idx]
/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data['data_category_number'][idx]
/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.

/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data['data_category_number'][idx]
/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data['data_category_number'][idx]
/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.

/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data['data_category_number'][idx]
/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data['data_category_number'][idx]
/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.

/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data['data_category_number'][idx]
/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data['data_category_number'][idx]
/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_87652/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.

...

 99%|██████████████████████████████████▊| 21325/21465 [5:07:57<02:01,  1.15it/s]


100%|██████████████████████████████████▉| 21422/21465 [5:09:21<00:37,  1.14it/s]


100%|███████████████████████████████████| 21465/21465 [5:11:23<00:00,  1.15it/s]


Here\s the fine-tuned model:  BertForSequenceClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(28996, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerN

OMP: Info #271: omp_set_nested routine deprecated, please use omp_set_max_active_levels instead.


In [41]:
# The following function is responsible for pretraining a masked bert model and fine-tuning the same pretrained model 
# (from huggingface) with a DSC dataset
def finetuneBertModelAfterPretrainingOfMaskedBertWithCustomDataset(input_file_name='ultra_clean_abstract_with_text.csv', 
                                         model_max_length=500,
                                         number_of_labels=19,
                                         number_of_epochs_for_masked_bert=2,
                                         number_of_epochs_for_finetuning_masked_bert=5                   
                                         output_file_name="something.json"):
    
    # Function that returns a new dataframe with reduced sentence sizes (as most bert models have a max_seq_length)
    data = updateDataFrame(input_file_name, model_max_length=model_max_length)
    print('Dataframe with reduced sentence sizes: \n')
    display(data)
    
    # Replacing all NaN fields under '2d_coor' column with an empty string
    print('Dataframe with NaN removed: \n')
    data['2d_coor'] = ''
    display(data)
    
    # Function that pretrains a masked bert model and saves that model in a directory: 'pytorch_model_unsupervised_finetuned'
    train_masked_bert(data, num_epochs=number_of_epochs_for_masked_bert, number_of_labels=number_of_labels)
    
    # Function that fine-tunes the above pretrained masked bert model
    new_model, score = fineTuneModelUnsupervised(df, number_of_labels=number_of_labels, number_of_epochs=number_of_epochs_for_finetuning_masked_bert)
    
    print('Here\s the fine-tuned model: ', model)
    print('Accuracy of the fine-tuned model on the test dataset is: ', score)
    
    # Function that returns the dataframe with embeddings (UMAP reduces high dimensional embedding to 2D)     
    data_with_embeddings = get_json_file(data, model, output_file_name)

SyntaxError: invalid syntax (3938428121.py, line 8)

In [50]:
def UMAPWithCustomDataset(input_file_name='Care_Reviews.csv', 
                        model_max_length=384,
                        output_json_file_name='test.json',
                         use_labels=True,
                         sentence_transformer_name='sentence-transformers/all-mpnet-base-v2'):
     # Function that returns a new dataframe with reduced sentence sizes (as most bert models have a max_seq_length)
    data = updateDataFrame(input_file_name, model_max_length=model_max_length)
    print('Dataframe with reduced sentence sizes: \n')
    display(data)
    
    # Replacing all NaN fields under '2d_coor' column with an empty string
    print('Dataframe with NaN removed: \n')
    data['2d_coor'] = ''
    display(data)
    
    # Using a bert model from sentence_transformers to generate embeddings
    from sentence_transformers import SentenceTransformer
    model = SentenceTransformer(sentence_transformer_name)
    sentences = data['data_string']
    embeddings_for_umap = model.encode(sentences)
    
    # Reducing the dimensionality of embeddings with UMAP
    import umap.umap_ as umap
    umap_embedding = umap.UMAP().fit_transform(embeddings_for_umap, y=list(data['data_category_number']) if use_labels else None)
    
    data['2d_coor'] = umap_embedding.tolist()
    display(data)
    
    list_of_points = []
    for idx in range(len(data['data_string'])):
        tmp_dict = {}
        tmp_dict["data_x"] = str(data['2d_coor'][idx][0])
        tmp_dict["data_y"] = str(data['2d_coor'][idx][1])
        tmp_dict["data_category_number"] = str(data['data_category_number'][idx])
        tmp_dict["data_id"] = str(data['data_id'][idx])

        tmp_dict["data_title"] = str(data['data_title'][idx])
        tmp_dict["data_category"] = str(data['data_category'][idx])

        list_of_points.append(tmp_dict)
        
    import json
    with open(output_json_file_name, "w") as outfile:
        json.dump(list_of_points, outfile)
        
    return data

In [53]:
d = UMAPWithCustomDataset(input_file_name='test_cleaned.csv', 
                        model_max_length=384,
                        output_json_file_name='test_umap.json',
                         use_labels=True)
d

/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_82464/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data['data_category_number'][idx]


Dataframe with reduced sentence sizes: 



data_id                                        data_string  2d_coor  \
0   15549400  Floral visitors vary in their pollination effi...      NaN   
1   25451119  This experiment investigated how the esthetic ...      NaN   
2   27236075  Women with high body dissatisfaction look less...      NaN   
3   15010496  We have used the technique of functional MRI t...      NaN   
4   18648595  Three aspects of hormesis with low doses of io...      NaN   
..       ...                                                ...      ...   
95   9874951  Children with severe and profound disabilities...      NaN   
96  18794733  As our ageing population demands to maintain y...      NaN   
97   3984466  This study reviews the cases of 49 patients wi...      NaN   
98  30231330  Acute myeloid leukemia (AML) was initially sub...      NaN   
99  27265766  The aesthetic experience through art is a wind...      NaN   

                                           data_title  data_category  \
0   Effects of low-efficiency pollinators on plant...            NaN   
1   Electrophysiological brain dynamics during the...            NaN   
2   Take a look at the bright side: Effects of pos...            NaN   
3                        Neural correlates of beauty.            NaN   
4   Radiation hormesis: the good, the bad, and the...            NaN   
..                                                ...            ...   
95  Children with severe and profound disabilities...            NaN   
96  "Ethics in aesthetic nursing...avoiding the ug...            NaN   
97  [Subcutaneous tenotomy of the sternocleidomast...            NaN   
98  Acute Myeloid Leukemia: The Good, the Bad, and...            NaN   
99  Ugly aesthetic perception associated with emot...            NaN   

    data_category_number  
0                    NaN  
1                    NaN  
2                    NaN  
3                    NaN  
4                    NaN  
..                   ...  
95                   NaN  
96                   NaN  
97                   NaN  
98                   NaN  
99                   NaN  

[100 rows x 6 columns]

Dataframe with NaN removed: 



data_id                                        data_string 2d_coor  \
0   15549400  Floral visitors vary in their pollination effi...           
1   25451119  This experiment investigated how the esthetic ...           
2   27236075  Women with high body dissatisfaction look less...           
3   15010496  We have used the technique of functional MRI t...           
4   18648595  Three aspects of hormesis with low doses of io...           
..       ...                                                ...     ...   
95   9874951  Children with severe and profound disabilities...           
96  18794733  As our ageing population demands to maintain y...           
97   3984466  This study reviews the cases of 49 patients wi...           
98  30231330  Acute myeloid leukemia (AML) was initially sub...           
99  27265766  The aesthetic experience through art is a wind...           

                                           data_title  data_category  \
0   Effects of low-efficiency pollinators on plant...            NaN   
1   Electrophysiological brain dynamics during the...            NaN   
2   Take a look at the bright side: Effects of pos...            NaN   
3                        Neural correlates of beauty.            NaN   
4   Radiation hormesis: the good, the bad, and the...            NaN   
..                                                ...            ...   
95  Children with severe and profound disabilities...            NaN   
96  "Ethics in aesthetic nursing...avoiding the ug...            NaN   
97  [Subcutaneous tenotomy of the sternocleidomast...            NaN   
98  Acute Myeloid Leukemia: The Good, the Bad, and...            NaN   
99  Ugly aesthetic perception associated with emot...            NaN   

    data_category_number  
0                    NaN  
1                    NaN  
2                    NaN  
3                    NaN  
4                    NaN  
..                   ...  
95                   NaN  
96                   NaN  
97                   NaN  
98                   NaN  
99                   NaN  

[100 rows x 6 columns]

  0%|                                                    | 0/50 [07:41<?, ?it/s]


ContextualVersionConflict: (numpy 1.23.0rc3 (/Users/ez/miniconda3/envs/torch-nightly/lib/python3.8/site-packages), Requirement.parse('numpy<1.23.0,>=1.16.5'), {'scipy'})

In [54]:
def TSNEWithCustomDataset(input_file_name='Care_Reviews.csv', 
                        model_max_length=384,
                        output_json_file_name='test.json',
                         sentence_transformer_name='all-MiniLM-L6-v2',
                         use_labels=True):
     # Function that returns a new dataframe with reduced sentence sizes (as most bert models have a max_seq_length)
    data = updateDataFrame(input_file_name, model_max_length=model_max_length)
    print('Dataframe with reduced sentence sizes: \n')
    display(data)
    
    # Replacing all NaN fields under '2d_coor' column with an empty string
    print('Dataframe with NaN removed: \n')
    data['2d_coor'] = ''
    display(data)
    
    # Using a bert model from sentence_transformers to generate embeddings
    from sentence_transformers import SentenceTransformer
    model = SentenceTransformer(sentence_transformer_name)
    sentences = data['data_string']
    embeddings_for_tsne = model.encode(sentences)
    
    # Reducing the dimensionality of embeddings with TSNE
    from sklearn.manifold import TSNE
    tsne = TSNE(n_components=2, verbose=1, perplexity=40, n_iter=300)
    tsne_results = tsne.fit_transform(embeddings_for_tsne, list(data['data_category_number']) if use_labels else None)
    
    data['2d_coor'] = tsne_results.tolist()
    display(data)
    
    list_of_points = []
    for idx in range(len(data['data_string'])):
        tmp_dict = {}
        tmp_dict["data_x"] = str(data['2d_coor'][idx][0])
        tmp_dict["data_y"] = str(data['2d_coor'][idx][1])
        tmp_dict["data_category_number"] = str(data['data_category_number'][idx])
        tmp_dict["data_id"] = str(data['data_id'][idx])

        tmp_dict["data_title"] = str(data['data_title'][idx])
        tmp_dict["data_category"] = str(data['data_category'][idx])

        list_of_points.append(tmp_dict)
        
    import json
    with open(output_json_file_name, "w") as outfile:
        json.dump(list_of_points, outfile)
        
    return data

In [21]:
d = TSNEWithCustomDataset(input_file_name='news_articles.csv', 
                        model_max_length=384,
                        output_json_file_name='news_articles_tsne.json',
                         sentence_transformer_name='all-MiniLM-L6-v2',
                         use_labels=True)
d

/tmp/ipykernel_3355/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data['data_category_number'][idx]


Dataframe with reduced sentence sizes: 



data_id                                        data_string  2d_coor  \
0           115  A collaboration between artist Christina Kelly...      NaN   
1           118  As Hurricane Irma draws closer to the Florida ...      NaN   
2           119  Raúl Ortega Ayala’s new exhibition at Proyecto...      NaN   
3           122  Welcome to the public markets, Snapchat. Stock...      NaN   
4           125  Vox Sentences is written by Dylan Matthews and...      NaN   
...         ...                                                ...      ...   
193487   813146  VNO's case approximately 90% of EBITDA will be...      NaN   
193488   813146  Individually or Collectively, Lead to Negative...      NaN   
193489   813146  THIS SITE. DIRECTORS AND SHAREHOLDERS RELEVANT...      NaN   
193490   813146  work of experts, including independent auditor...      NaN   
193491   813146  to US$750,000 (or the applicable currency equi...      NaN   

                                               data_title  \
0            The History of Gowanus Cemented in Sculpture   
1       Emergency Services Rush to Save Expensive Wine...   
2       An Artist Serves Up Food for Thought About Exc...   
3       Snap stock took a beating Monday and fell more...   
4        Vox Sentences: There’s a coup underway in Turkey   
...                                                   ...   
193487  Fitch Affirms American Assets Trust's IDR at '...   
193488  Fitch Affirms American Assets Trust's IDR at '...   
193489  Fitch Affirms American Assets Trust's IDR at '...   
193490  Fitch Affirms American Assets Trust's IDR at '...   
193491  Fitch Affirms American Assets Trust's IDR at '...   

                                            data_category  \
0       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
1       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
2       0.005*"colbert" + 0.005*"corden" + 0.004*"week...   
3       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
4       0.005*"percent" + 0.004*"reuters" + 0.004*"com...   
...                                                   ...   
193487  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193488  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193489  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193490  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193491  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   

        data_category_number  
0                         11  
1                         11  
2                          7  
3                         11  
4                         12  
...                      ...  
193487                     4  
193488                     4  
193489                     4  
193490                     4  
193491                     4  

[193492 rows x 6 columns]

Dataframe with NaN removed: 



data_id                                        data_string 2d_coor  \
0           115  A collaboration between artist Christina Kelly...           
1           118  As Hurricane Irma draws closer to the Florida ...           
2           119  Raúl Ortega Ayala’s new exhibition at Proyecto...           
3           122  Welcome to the public markets, Snapchat. Stock...           
4           125  Vox Sentences is written by Dylan Matthews and...           
...         ...                                                ...     ...   
193487   813146  VNO's case approximately 90% of EBITDA will be...           
193488   813146  Individually or Collectively, Lead to Negative...           
193489   813146  THIS SITE. DIRECTORS AND SHAREHOLDERS RELEVANT...           
193490   813146  work of experts, including independent auditor...           
193491   813146  to US$750,000 (or the applicable currency equi...           

                                               data_title  \
0            The History of Gowanus Cemented in Sculpture   
1       Emergency Services Rush to Save Expensive Wine...   
2       An Artist Serves Up Food for Thought About Exc...   
3       Snap stock took a beating Monday and fell more...   
4        Vox Sentences: There’s a coup underway in Turkey   
...                                                   ...   
193487  Fitch Affirms American Assets Trust's IDR at '...   
193488  Fitch Affirms American Assets Trust's IDR at '...   
193489  Fitch Affirms American Assets Trust's IDR at '...   
193490  Fitch Affirms American Assets Trust's IDR at '...   
193491  Fitch Affirms American Assets Trust's IDR at '...   

                                            data_category  \
0       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
1       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
2       0.005*"colbert" + 0.005*"corden" + 0.004*"week...   
3       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
4       0.005*"percent" + 0.004*"reuters" + 0.004*"com...   
...                                                   ...   
193487  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193488  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193489  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193490  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193491  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   

        data_category_number  
0                         11  
1                         11  
2                          7  
3                         11  
4                         12  
...                      ...  
193487                     4  
193488                     4  
193489                     4  
193490                     4  
193491                     4  

[193492 rows x 6 columns]

/home/ubuntu/venv/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:780: FutureWarning: The default initialization in TSNE will change from 'random' to 'pca' in 1.2.
  warnings.warn(
/home/ubuntu/venv/lib/python3.8/site-packages/sklearn/manifold/_t_sne.py:790: FutureWarning: The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.
  warnings.warn(


[t-SNE] Computing 121 nearest neighbors...
[t-SNE] Indexed 193492 samples in 0.069s...
[t-SNE] Computed neighbors for 193492 samples in 1197.803s...
[t-SNE] Computed conditional probabilities for sample 1000 / 193492
[t-SNE] Computed conditional probabilities for sample 2000 / 193492
[t-SNE] Computed conditional probabilities for sample 3000 / 193492
[t-SNE] Computed conditional probabilities for sample 4000 / 193492
[t-SNE] Computed conditional probabilities for sample 5000 / 193492
[t-SNE] Computed conditional probabilities for sample 6000 / 193492
[t-SNE] Computed conditional probabilities for sample 7000 / 193492
[t-SNE] Computed conditional probabilities for sample 8000 / 193492
[t-SNE] Computed conditional probabilities for sample 9000 / 193492
[t-SNE] Computed conditional probabilities for sample 10000 / 193492
[t-SNE] Computed conditional probabilities for sample 11000 / 193492
[t-SNE] Computed conditional probabilities for sample 12000 / 193492
[t-SNE] Computed conditional pro

[t-SNE] Computed conditional probabilities for sample 118000 / 193492
[t-SNE] Computed conditional probabilities for sample 119000 / 193492
[t-SNE] Computed conditional probabilities for sample 120000 / 193492
[t-SNE] Computed conditional probabilities for sample 121000 / 193492
[t-SNE] Computed conditional probabilities for sample 122000 / 193492
[t-SNE] Computed conditional probabilities for sample 123000 / 193492
[t-SNE] Computed conditional probabilities for sample 124000 / 193492
[t-SNE] Computed conditional probabilities for sample 125000 / 193492
[t-SNE] Computed conditional probabilities for sample 126000 / 193492
[t-SNE] Computed conditional probabilities for sample 127000 / 193492
[t-SNE] Computed conditional probabilities for sample 128000 / 193492
[t-SNE] Computed conditional probabilities for sample 129000 / 193492
[t-SNE] Computed conditional probabilities for sample 130000 / 193492
[t-SNE] Computed conditional probabilities for sample 131000 / 193492
[t-SNE] Computed con

data_id                                        data_string  \
0           115  A collaboration between artist Christina Kelly...   
1           118  As Hurricane Irma draws closer to the Florida ...   
2           119  Raúl Ortega Ayala’s new exhibition at Proyecto...   
3           122  Welcome to the public markets, Snapchat. Stock...   
4           125  Vox Sentences is written by Dylan Matthews and...   
...         ...                                                ...   
193487   813146  VNO's case approximately 90% of EBITDA will be...   
193488   813146  Individually or Collectively, Lead to Negative...   
193489   813146  THIS SITE. DIRECTORS AND SHAREHOLDERS RELEVANT...   
193490   813146  work of experts, including independent auditor...   
193491   813146  to US$750,000 (or the applicable currency equi...   

                                          2d_coor  \
0        [4.397582054138184, -3.5684354305267334]   
1         [-0.3279964327812195, 8.61110782623291]   
2         [4.169193744659424, -4.005739212036133]   
3       [-2.864100933074951, -0.9488449692726135]   
4           [0.2897432744503021, 10.175537109375]   
...                                           ...   
193487    [-5.589747428894043, 3.172562599182129]   
193488       [4.083289623260498, 9.9985933303833]   
193489    [4.8006367683410645, 9.934613227844238]   
193490     [4.684049606323242, 9.922048568725586]   
193491   [12.157347679138184, 0.8815428614616394]   

                                               data_title  \
0            The History of Gowanus Cemented in Sculpture   
1       Emergency Services Rush to Save Expensive Wine...   
2       An Artist Serves Up Food for Thought About Exc...   
3       Snap stock took a beating Monday and fell more...   
4        Vox Sentences: There’s a coup underway in Turkey   
...                                                   ...   
193487  Fitch Affirms American Assets Trust's IDR at '...   
193488  Fitch Affirms American Assets Trust's IDR at '...   
193489  Fitch Affirms American Assets Trust's IDR at '...   
193490  Fitch Affirms American Assets Trust's IDR at '...   
193491  Fitch Affirms American Assets Trust's IDR at '...   

                                            data_category  \
0       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
1       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
2       0.005*"colbert" + 0.005*"corden" + 0.004*"week...   
3       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
4       0.005*"percent" + 0.004*"reuters" + 0.004*"com...   
...                                                   ...   
193487  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193488  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193489  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193490  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193491  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   

        data_category_number  
0                         11  
1                         11  
2                          7  
3                         11  
4                         12  
...                      ...  
193487                     4  
193488                     4  
193489                     4  
193490                     4  
193491                     4  

[193492 rows x 6 columns]

data_id                                        data_string  \
0           115  A collaboration between artist Christina Kelly...   
1           118  As Hurricane Irma draws closer to the Florida ...   
2           119  Raúl Ortega Ayala’s new exhibition at Proyecto...   
3           122  Welcome to the public markets, Snapchat. Stock...   
4           125  Vox Sentences is written by Dylan Matthews and...   
...         ...                                                ...   
193487   813146  VNO's case approximately 90% of EBITDA will be...   
193488   813146  Individually or Collectively, Lead to Negative...   
193489   813146  THIS SITE. DIRECTORS AND SHAREHOLDERS RELEVANT...   
193490   813146  work of experts, including independent auditor...   
193491   813146  to US$750,000 (or the applicable currency equi...   

                                          2d_coor  \
0        [4.397582054138184, -3.5684354305267334]   
1         [-0.3279964327812195, 8.61110782623291]   
2         [4.169193744659424, -4.005739212036133]   
3       [-2.864100933074951, -0.9488449692726135]   
4           [0.2897432744503021, 10.175537109375]   
...                                           ...   
193487    [-5.589747428894043, 3.172562599182129]   
193488       [4.083289623260498, 9.9985933303833]   
193489    [4.8006367683410645, 9.934613227844238]   
193490     [4.684049606323242, 9.922048568725586]   
193491   [12.157347679138184, 0.8815428614616394]   

                                               data_title  \
0            The History of Gowanus Cemented in Sculpture   
1       Emergency Services Rush to Save Expensive Wine...   
2       An Artist Serves Up Food for Thought About Exc...   
3       Snap stock took a beating Monday and fell more...   
4        Vox Sentences: There’s a coup underway in Turkey   
...                                                   ...   
193487  Fitch Affirms American Assets Trust's IDR at '...   
193488  Fitch Affirms American Assets Trust's IDR at '...   
193489  Fitch Affirms American Assets Trust's IDR at '...   
193490  Fitch Affirms American Assets Trust's IDR at '...   
193491  Fitch Affirms American Assets Trust's IDR at '...   

                                            data_category  \
0       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
1       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
2       0.005*"colbert" + 0.005*"corden" + 0.004*"week...   
3       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
4       0.005*"percent" + 0.004*"reuters" + 0.004*"com...   
...                                                   ...   
193487  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193488  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193489  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193490  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193491  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   

        data_category_number  
0                         11  
1                         11  
2                          7  
3                         11  
4                         12  
...                      ...  
193487                     4  
193488                     4  
193489                     4  
193490                     4  
193491                     4  

[193492 rows x 6 columns]

In [56]:
def PCAWithCustomDataset(input_file_name='Care_Reviews.csv', 
                        model_max_length=384,
                        output_json_file_name='test.json',
                         sentence_transformer_name='all-MiniLM-L6-v2',
                        p_components=2,
                        use_labels=True):
     # Function that returns a new dataframe with reduced sentence sizes (as most bert models have a max_seq_length)
    data = updateDataFrame(input_file_name, model_max_length=model_max_length)
    print('Dataframe with reduced sentence sizes: \n')
    display(data)
    
    # Replacing all NaN fields under '2d_coor' column with an empty string
    print('Dataframe with NaN removed: \n')
    data['2d_coor'] = ''
    display(data)
    
    # Using a bert model from sentence_transformers to generate embeddings
    from sentence_transformers import SentenceTransformer
    model = SentenceTransformer(sentence_transformer_name)
    sentences = data['data_string']
    embeddings_for_pca = model.encode(sentences)
    
    # Reducing the dimensionality of embeddings with PCA
    from sklearn.decomposition import PCA

    pca_2d_class = PCA(n_components=p_components).fit(embeddings_for_pca, list(data['data_category_number']) if use_labels else None)

    pca_2d = pca_2d_class.transform(embeddings_for_pca)
    
    data['2d_coor'] = pca_2d.tolist()
    display(data)
    
    
    list_of_points = []
    for idx in range(len(data['data_string'])):
        tmp_dict = {}
        tmp_dict["data_x"] = str(data['2d_coor'][idx][0])
        tmp_dict["data_y"] = str(data['2d_coor'][idx][1])
        tmp_dict["data_category_number"] = str(data['data_category_number'][idx])
        tmp_dict["data_id"] = str(data['data_id'][idx])

        tmp_dict["data_title"] = str(data['data_title'][idx])
        tmp_dict["data_category"] = str(data['data_category'][idx])

        list_of_points.append(tmp_dict)
        
    import json
    with open(output_json_file_name, "w") as outfile:
        json.dump(list_of_points, outfile)
        
    return data

In [57]:
d = PCAWithCustomDataset(input_file_name='test_lda.csv', 
                        model_max_length=384,
                        output_json_file_name='test_pca.json',
                         sentence_transformer_name='all-MiniLM-L6-v2',
                        p_components=2,
                        use_labels=True)
d

/var/folders/2k/s5r6t0jx06n0jzv1j1d39ns00000gr/T/ipykernel_82464/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data['data_category_number'][idx]


Dataframe with reduced sentence sizes: 



data_id                                        data_string  2d_coor  \
0   15549400  Floral visitors vary in their pollination effi...      NaN   
1   25451119  This experiment investigated how the esthetic ...      NaN   
2   27236075  Women with high body dissatisfaction look less...      NaN   
3   15010496  We have used the technique of functional MRI t...      NaN   
4   18648595  Three aspects of hormesis with low doses of io...      NaN   
..       ...                                                ...      ...   
95   9874951  Children with severe and profound disabilities...      NaN   
96  18794733  As our ageing population demands to maintain y...      NaN   
97   3984466  This study reviews the cases of 49 patients wi...      NaN   
98  30231330  Acute myeloid leukemia (AML) was initially sub...      NaN   
99  27265766  The aesthetic experience through art is a wind...      NaN   

                                           data_title  \
0   Effects of low-efficiency pollinators on plant...   
1   Electrophysiological brain dynamics during the...   
2   Take a look at the bright side: Effects of pos...   
3                        Neural correlates of beauty.   
4   Radiation hormesis: the good, the bad, and the...   
..                                                ...   
95  Children with severe and profound disabilities...   
96  "Ethics in aesthetic nursing...avoiding the ug...   
97  [Subcutaneous tenotomy of the sternocleidomast...   
98  Acute Myeloid Leukemia: The Good, the Bad, and...   
99  Ugly aesthetic perception associated with emot...   

                                        data_category  data_category_number  
0   0.004*"mood" + 0.003*"backfilling" + 0.002*"in...                   4.0  
1   0.003*"challenging" + 0.003*"bonds" + 0.003*"c...                   7.0  
2   0.004*"parallel" + 0.003*"work" + 0.003*"herba...                   9.0  
3   0.003*"challenging" + 0.003*"bonds" + 0.003*"c...                   7.0  
4   0.005*"failure" + 0.004*"pollinators" + 0.003*...                   5.0  
..                                                ...                   ...  
95  0.003*"disabilities" + 0.003*"aesthetic" + 0.0...                   3.0  
96  0.004*"west" + 0.003*"nonsurgical" + 0.002*"ae...                   1.0  
97  0.003*"challenging" + 0.003*"bonds" + 0.003*"c...                   7.0  
98  0.004*"mood" + 0.003*"backfilling" + 0.002*"in...                   4.0  
99  0.003*"disabilities" + 0.003*"aesthetic" + 0.0...                   3.0  

[100 rows x 6 columns]

Dataframe with NaN removed: 



data_id                                        data_string 2d_coor  \
0   15549400  Floral visitors vary in their pollination effi...           
1   25451119  This experiment investigated how the esthetic ...           
2   27236075  Women with high body dissatisfaction look less...           
3   15010496  We have used the technique of functional MRI t...           
4   18648595  Three aspects of hormesis with low doses of io...           
..       ...                                                ...     ...   
95   9874951  Children with severe and profound disabilities...           
96  18794733  As our ageing population demands to maintain y...           
97   3984466  This study reviews the cases of 49 patients wi...           
98  30231330  Acute myeloid leukemia (AML) was initially sub...           
99  27265766  The aesthetic experience through art is a wind...           

                                           data_title  \
0   Effects of low-efficiency pollinators on plant...   
1   Electrophysiological brain dynamics during the...   
2   Take a look at the bright side: Effects of pos...   
3                        Neural correlates of beauty.   
4   Radiation hormesis: the good, the bad, and the...   
..                                                ...   
95  Children with severe and profound disabilities...   
96  "Ethics in aesthetic nursing...avoiding the ug...   
97  [Subcutaneous tenotomy of the sternocleidomast...   
98  Acute Myeloid Leukemia: The Good, the Bad, and...   
99  Ugly aesthetic perception associated with emot...   

                                        data_category  data_category_number  
0   0.004*"mood" + 0.003*"backfilling" + 0.002*"in...                   4.0  
1   0.003*"challenging" + 0.003*"bonds" + 0.003*"c...                   7.0  
2   0.004*"parallel" + 0.003*"work" + 0.003*"herba...                   9.0  
3   0.003*"challenging" + 0.003*"bonds" + 0.003*"c...                   7.0  
4   0.005*"failure" + 0.004*"pollinators" + 0.003*...                   5.0  
..                                                ...                   ...  
95  0.003*"disabilities" + 0.003*"aesthetic" + 0.0...                   3.0  
96  0.004*"west" + 0.003*"nonsurgical" + 0.002*"ae...                   1.0  
97  0.003*"challenging" + 0.003*"bonds" + 0.003*"c...                   7.0  
98  0.004*"mood" + 0.003*"backfilling" + 0.002*"in...                   4.0  
99  0.003*"disabilities" + 0.003*"aesthetic" + 0.0...                   3.0  

[100 rows x 6 columns]

Downloading: 100%|██████████████████████████| 1.18k/1.18k [00:00<00:00, 228kB/s]
Downloading: 100%|█████████████████████████████| 190/190 [00:00<00:00, 56.2kB/s]
Downloading: 100%|█████████████████████████| 10.2k/10.2k [00:00<00:00, 2.15MB/s]
Downloading: 100%|█████████████████████████████| 116/116 [00:00<00:00, 19.1kB/s]
Downloading: 100%|██████████████████████████| 39.3k/39.3k [00:00<00:00, 642kB/s]
Downloading: 100%|█████████████████████████| 90.9M/90.9M [00:09<00:00, 9.44MB/s]
Downloading: 100%|███████████████████████████| 53.0/53.0 [00:00<00:00, 6.57kB/s]
Downloading: 100%|█████████████████████████████| 112/112 [00:00<00:00, 21.1kB/s]
Downloading: 100%|███████████████████████████| 466k/466k [00:00<00:00, 1.59MB/s]
Downloading: 100%|█████████████████████████████| 350/350 [00:00<00:00, 36.8kB/s]
Downloading: 100%|█████████████████████████| 13.2k/13.2k [00:00<00:00, 2.14MB/s]
Downloading: 100%|███████████████████████████| 232k/232k [00:00<00:00, 1.34MB/s]
Downloading: 100%|██████████

data_id                                        data_string  \
0   15549400  Floral visitors vary in their pollination effi...   
1   25451119  This experiment investigated how the esthetic ...   
2   27236075  Women with high body dissatisfaction look less...   
3   15010496  We have used the technique of functional MRI t...   
4   18648595  Three aspects of hormesis with low doses of io...   
..       ...                                                ...   
95   9874951  Children with severe and profound disabilities...   
96  18794733  As our ageing population demands to maintain y...   
97   3984466  This study reviews the cases of 49 patients wi...   
98  30231330  Acute myeloid leukemia (AML) was initially sub...   
99  27265766  The aesthetic experience through art is a wind...   

                                         2d_coor  \
0    [0.27713698148727417, -0.10882366448640823]   
1      [0.5933237075805664, 0.09017793834209442]   
2     [0.5550868511199951, 0.047366585582494736]   
3      [0.4833657741546631, 0.09579300880432129]   
4    [-0.14024655520915985, -0.2112492322921753]   
..                                           ...   
95  [-0.21721360087394714, -0.22595451772212982]   
96   [0.06945352256298065, -0.00463707372546196]   
97    [-0.3445499837398529, 0.38034558296203613]   
98  [-0.20531556010246277, -0.16500544548034668]   
99     [0.4516730308532715, 0.01466207392513752]   

                                           data_title  \
0   Effects of low-efficiency pollinators on plant...   
1   Electrophysiological brain dynamics during the...   
2   Take a look at the bright side: Effects of pos...   
3                        Neural correlates of beauty.   
4   Radiation hormesis: the good, the bad, and the...   
..                                                ...   
95  Children with severe and profound disabilities...   
96  "Ethics in aesthetic nursing...avoiding the ug...   
97  [Subcutaneous tenotomy of the sternocleidomast...   
98  Acute Myeloid Leukemia: The Good, the Bad, and...   
99  Ugly aesthetic perception associated with emot...   

                                        data_category  data_category_number  
0   0.004*"mood" + 0.003*"backfilling" + 0.002*"in...                   4.0  
1   0.003*"challenging" + 0.003*"bonds" + 0.003*"c...                   7.0  
2   0.004*"parallel" + 0.003*"work" + 0.003*"herba...                   9.0  
3   0.003*"challenging" + 0.003*"bonds" + 0.003*"c...                   7.0  
4   0.005*"failure" + 0.004*"pollinators" + 0.003*...                   5.0  
..                                                ...                   ...  
95  0.003*"disabilities" + 0.003*"aesthetic" + 0.0...                   3.0  
96  0.004*"west" + 0.003*"nonsurgical" + 0.002*"ae...                   1.0  
97  0.003*"challenging" + 0.003*"bonds" + 0.003*"c...                   7.0  
98  0.004*"mood" + 0.003*"backfilling" + 0.002*"in...                   4.0  
99  0.003*"disabilities" + 0.003*"aesthetic" + 0.0...                   3.0  

[100 rows x 6 columns]

data_id                                        data_string  \
0   15549400  Floral visitors vary in their pollination effi...   
1   25451119  This experiment investigated how the esthetic ...   
2   27236075  Women with high body dissatisfaction look less...   
3   15010496  We have used the technique of functional MRI t...   
4   18648595  Three aspects of hormesis with low doses of io...   
..       ...                                                ...   
95   9874951  Children with severe and profound disabilities...   
96  18794733  As our ageing population demands to maintain y...   
97   3984466  This study reviews the cases of 49 patients wi...   
98  30231330  Acute myeloid leukemia (AML) was initially sub...   
99  27265766  The aesthetic experience through art is a wind...   

                                         2d_coor  \
0    [0.27713698148727417, -0.10882366448640823]   
1      [0.5933237075805664, 0.09017793834209442]   
2     [0.5550868511199951, 0.047366585582494736]   
3      [0.4833657741546631, 0.09579300880432129]   
4    [-0.14024655520915985, -0.2112492322921753]   
..                                           ...   
95  [-0.21721360087394714, -0.22595451772212982]   
96   [0.06945352256298065, -0.00463707372546196]   
97    [-0.3445499837398529, 0.38034558296203613]   
98  [-0.20531556010246277, -0.16500544548034668]   
99     [0.4516730308532715, 0.01466207392513752]   

                                           data_title  \
0   Effects of low-efficiency pollinators on plant...   
1   Electrophysiological brain dynamics during the...   
2   Take a look at the bright side: Effects of pos...   
3                        Neural correlates of beauty.   
4   Radiation hormesis: the good, the bad, and the...   
..                                                ...   
95  Children with severe and profound disabilities...   
96  "Ethics in aesthetic nursing...avoiding the ug...   
97  [Subcutaneous tenotomy of the sternocleidomast...   
98  Acute Myeloid Leukemia: The Good, the Bad, and...   
99  Ugly aesthetic perception associated with emot...   

                                        data_category  data_category_number  
0   0.004*"mood" + 0.003*"backfilling" + 0.002*"in...                   4.0  
1   0.003*"challenging" + 0.003*"bonds" + 0.003*"c...                   7.0  
2   0.004*"parallel" + 0.003*"work" + 0.003*"herba...                   9.0  
3   0.003*"challenging" + 0.003*"bonds" + 0.003*"c...                   7.0  
4   0.005*"failure" + 0.004*"pollinators" + 0.003*...                   5.0  
..                                                ...                   ...  
95  0.003*"disabilities" + 0.003*"aesthetic" + 0.0...                   3.0  
96  0.004*"west" + 0.003*"nonsurgical" + 0.002*"ae...                   1.0  
97  0.003*"challenging" + 0.003*"bonds" + 0.003*"c...                   7.0  
98  0.004*"mood" + 0.003*"backfilling" + 0.002*"in...                   4.0  
99  0.003*"disabilities" + 0.003*"aesthetic" + 0.0...                   3.0  

[100 rows x 6 columns]

In [32]:
def KMeansAndPCAWithCustomDataset(input_file_name='Care_Reviews.csv', 
                        model_max_length=384,
                        output_json_file_name='test.json',
                         sentence_transformer_name='all-MiniLM-L6-v2',
                        p_components=2,
                        # Keep use_labels=True always for KMeans+PCA (reason: there can be countless clusters without labels)                                   
                        use_labels=True):
     # Function that returns a new dataframe with reduced sentence sizes (as most bert models have a max_seq_length)
    data = updateDataFrame(input_file_name, model_max_length=model_max_length)
    print('Dataframe with reduced sentence sizes: \n')
    display(data)
    
    # Replacing all NaN fields under '2d_coor' column with an empty string
    print('Dataframe with NaN removed: \n')
    data['2d_coor'] = ''
    display(data)
    
    # Using a bert model from sentence_transformers to generate embeddings
    from sentence_transformers import SentenceTransformer
    model = SentenceTransformer(sentence_transformer_name)
    sentences = data['data_string']
    embeddings_for_kmeans = model.encode(sentences)
    
    # Reducing the dimensionality of embeddings with PCA After applying KMeans
    from sklearn.cluster import KMeans
    from sklearn.decomposition import PCA
    
    kmeans = KMeans(n_clusters=len(data['data_category_number'].unique()))
    labels = kmeans.fit_predict(embeddings_for_kmeans, list(data['data_category_number']) if use_labels else None)
    labels_scale = kmeans.labels_

    pca_2d_class = PCA(n_components=p_components).fit(embeddings_for_kmeans, labels.tolist())

    pca_2d = pca_2d_class.transform(embeddings_for_kmeans)
    
    data['2d_coor'] = pca_2d.tolist()
    display(data)
    
    new_labels = labels.tolist()
    list_of_points = []
    for idx in range(len(data['data_string'])):
        tmp_dict = {}
        tmp_dict["data_x"] = str(data['2d_coor'][idx][0])
        tmp_dict["data_y"] = str(data['2d_coor'][idx][1])
#         tmp_dict["data_category_number"] = str(data['data_category_number'][idx])
        tmp_dict["data_category_number"] = str(new_labels[idx])
        tmp_dict["data_id"] = str(data['data_id'][idx])

        tmp_dict["data_title"] = str(data['data_title'][idx])
        tmp_dict["data_category"] = str(data['data_category'][idx])

        list_of_points.append(tmp_dict)
        
    import json
    with open(output_json_file_name, "w") as outfile:
        json.dump(list_of_points, outfile)
        
    return data

In [33]:
d = KMeansAndPCAWithCustomDataset(input_file_name='news_articles.csv', 
                        model_max_length=384,
                        output_json_file_name='news_articles_kmeanspca.json',
                         sentence_transformer_name='all-MiniLM-L6-v2',
                        p_components=2,
                        # Keep use_labels=True always for KMeans+PCA (reason: there can be countless clusters without labels)                                   
                        use_labels=True)
d

/tmp/ipykernel_1741/1359901329.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data['data_category_number'][idx] = data['data_category_number'][idx]


Dataframe with reduced sentence sizes: 



data_id                                        data_string  2d_coor  \
0           115  A collaboration between artist Christina Kelly...      NaN   
1           118  As Hurricane Irma draws closer to the Florida ...      NaN   
2           119  Raúl Ortega Ayala’s new exhibition at Proyecto...      NaN   
3           122  Welcome to the public markets, Snapchat. Stock...      NaN   
4           125  Vox Sentences is written by Dylan Matthews and...      NaN   
...         ...                                                ...      ...   
193487   813146  VNO's case approximately 90% of EBITDA will be...      NaN   
193488   813146  Individually or Collectively, Lead to Negative...      NaN   
193489   813146  THIS SITE. DIRECTORS AND SHAREHOLDERS RELEVANT...      NaN   
193490   813146  work of experts, including independent auditor...      NaN   
193491   813146  to US$750,000 (or the applicable currency equi...      NaN   

                                               data_title  \
0            The History of Gowanus Cemented in Sculpture   
1       Emergency Services Rush to Save Expensive Wine...   
2       An Artist Serves Up Food for Thought About Exc...   
3       Snap stock took a beating Monday and fell more...   
4        Vox Sentences: There’s a coup underway in Turkey   
...                                                   ...   
193487  Fitch Affirms American Assets Trust's IDR at '...   
193488  Fitch Affirms American Assets Trust's IDR at '...   
193489  Fitch Affirms American Assets Trust's IDR at '...   
193490  Fitch Affirms American Assets Trust's IDR at '...   
193491  Fitch Affirms American Assets Trust's IDR at '...   

                                            data_category  \
0       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
1       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
2       0.005*"colbert" + 0.005*"corden" + 0.004*"week...   
3       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
4       0.005*"percent" + 0.004*"reuters" + 0.004*"com...   
...                                                   ...   
193487  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193488  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193489  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193490  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193491  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   

        data_category_number  
0                         11  
1                         11  
2                          7  
3                         11  
4                         12  
...                      ...  
193487                     4  
193488                     4  
193489                     4  
193490                     4  
193491                     4  

[193492 rows x 6 columns]

Dataframe with NaN removed: 



data_id                                        data_string 2d_coor  \
0           115  A collaboration between artist Christina Kelly...           
1           118  As Hurricane Irma draws closer to the Florida ...           
2           119  Raúl Ortega Ayala’s new exhibition at Proyecto...           
3           122  Welcome to the public markets, Snapchat. Stock...           
4           125  Vox Sentences is written by Dylan Matthews and...           
...         ...                                                ...     ...   
193487   813146  VNO's case approximately 90% of EBITDA will be...           
193488   813146  Individually or Collectively, Lead to Negative...           
193489   813146  THIS SITE. DIRECTORS AND SHAREHOLDERS RELEVANT...           
193490   813146  work of experts, including independent auditor...           
193491   813146  to US$750,000 (or the applicable currency equi...           

                                               data_title  \
0            The History of Gowanus Cemented in Sculpture   
1       Emergency Services Rush to Save Expensive Wine...   
2       An Artist Serves Up Food for Thought About Exc...   
3       Snap stock took a beating Monday and fell more...   
4        Vox Sentences: There’s a coup underway in Turkey   
...                                                   ...   
193487  Fitch Affirms American Assets Trust's IDR at '...   
193488  Fitch Affirms American Assets Trust's IDR at '...   
193489  Fitch Affirms American Assets Trust's IDR at '...   
193490  Fitch Affirms American Assets Trust's IDR at '...   
193491  Fitch Affirms American Assets Trust's IDR at '...   

                                            data_category  \
0       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
1       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
2       0.005*"colbert" + 0.005*"corden" + 0.004*"week...   
3       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
4       0.005*"percent" + 0.004*"reuters" + 0.004*"com...   
...                                                   ...   
193487  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193488  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193489  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193490  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193491  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   

        data_category_number  
0                         11  
1                         11  
2                          7  
3                         11  
4                         12  
...                      ...  
193487                     4  
193488                     4  
193489                     4  
193490                     4  
193491                     4  

[193492 rows x 6 columns]

data_id                                        data_string  \
0           115  A collaboration between artist Christina Kelly...   
1           118  As Hurricane Irma draws closer to the Florida ...   
2           119  Raúl Ortega Ayala’s new exhibition at Proyecto...   
3           122  Welcome to the public markets, Snapchat. Stock...   
4           125  Vox Sentences is written by Dylan Matthews and...   
...         ...                                                ...   
193487   813146  VNO's case approximately 90% of EBITDA will be...   
193488   813146  Individually or Collectively, Lead to Negative...   
193489   813146  THIS SITE. DIRECTORS AND SHAREHOLDERS RELEVANT...   
193490   813146  work of experts, including independent auditor...   
193491   813146  to US$750,000 (or the applicable currency equi...   

                                              2d_coor  \
0         [-0.21102222800254822, -0.1435994803905487]   
1           [0.1290389597415924, 0.03235282376408577]   
2        [-0.14857149124145508, -0.17933329939842224]   
3           [0.3369511067867279, -0.1775447428226471]   
4       [-0.026973845437169075, 0.012201634235680103]   
...                                               ...   
193487      [0.3518417477607727, -0.1885872483253479]   
193488     [0.3118555545806885, -0.04097635671496391]   
193489      [0.1637514978647232, 0.08637033402919769]   
193490     [0.14689454436302185, 0.08255422115325928]   
193491    [0.29277899861335754, -0.10368742793798447]   

                                               data_title  \
0            The History of Gowanus Cemented in Sculpture   
1       Emergency Services Rush to Save Expensive Wine...   
2       An Artist Serves Up Food for Thought About Exc...   
3       Snap stock took a beating Monday and fell more...   
4        Vox Sentences: There’s a coup underway in Turkey   
...                                                   ...   
193487  Fitch Affirms American Assets Trust's IDR at '...   
193488  Fitch Affirms American Assets Trust's IDR at '...   
193489  Fitch Affirms American Assets Trust's IDR at '...   
193490  Fitch Affirms American Assets Trust's IDR at '...   
193491  Fitch Affirms American Assets Trust's IDR at '...   

                                            data_category  \
0       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
1       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
2       0.005*"colbert" + 0.005*"corden" + 0.004*"week...   
3       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
4       0.005*"percent" + 0.004*"reuters" + 0.004*"com...   
...                                                   ...   
193487  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193488  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193489  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193490  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193491  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   

        data_category_number  
0                         11  
1                         11  
2                          7  
3                         11  
4                         12  
...                      ...  
193487                     4  
193488                     4  
193489                     4  
193490                     4  
193491                     4  

[193492 rows x 6 columns]

data_id                                        data_string  \
0           115  A collaboration between artist Christina Kelly...   
1           118  As Hurricane Irma draws closer to the Florida ...   
2           119  Raúl Ortega Ayala’s new exhibition at Proyecto...   
3           122  Welcome to the public markets, Snapchat. Stock...   
4           125  Vox Sentences is written by Dylan Matthews and...   
...         ...                                                ...   
193487   813146  VNO's case approximately 90% of EBITDA will be...   
193488   813146  Individually or Collectively, Lead to Negative...   
193489   813146  THIS SITE. DIRECTORS AND SHAREHOLDERS RELEVANT...   
193490   813146  work of experts, including independent auditor...   
193491   813146  to US$750,000 (or the applicable currency equi...   

                                              2d_coor  \
0         [-0.21102222800254822, -0.1435994803905487]   
1           [0.1290389597415924, 0.03235282376408577]   
2        [-0.14857149124145508, -0.17933329939842224]   
3           [0.3369511067867279, -0.1775447428226471]   
4       [-0.026973845437169075, 0.012201634235680103]   
...                                               ...   
193487      [0.3518417477607727, -0.1885872483253479]   
193488     [0.3118555545806885, -0.04097635671496391]   
193489      [0.1637514978647232, 0.08637033402919769]   
193490     [0.14689454436302185, 0.08255422115325928]   
193491    [0.29277899861335754, -0.10368742793798447]   

                                               data_title  \
0            The History of Gowanus Cemented in Sculpture   
1       Emergency Services Rush to Save Expensive Wine...   
2       An Artist Serves Up Food for Thought About Exc...   
3       Snap stock took a beating Monday and fell more...   
4        Vox Sentences: There’s a coup underway in Turkey   
...                                                   ...   
193487  Fitch Affirms American Assets Trust's IDR at '...   
193488  Fitch Affirms American Assets Trust's IDR at '...   
193489  Fitch Affirms American Assets Trust's IDR at '...   
193490  Fitch Affirms American Assets Trust's IDR at '...   
193491  Fitch Affirms American Assets Trust's IDR at '...   

                                            data_category  \
0       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
1       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
2       0.005*"colbert" + 0.005*"corden" + 0.004*"week...   
3       0.003*"apple" + 0.003*"facebook" + 0.002*"goog...   
4       0.005*"percent" + 0.004*"reuters" + 0.004*"com...   
...                                                   ...   
193487  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193488  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193489  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193490  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   
193491  0.011*"million" + 0.009*"versus" + 0.009*"eiko...   

        data_category_number  
0                         11  
1                         11  
2                          7  
3                         11  
4                         12  
...                      ...  
193487                     4  
193488                     4  
193489                     4  
193490                     4  
193491                     4  

[193492 rows x 6 columns]

In [ ]:
def PCAAndKMeansWithCustomDataset(input_file_name='Care_Reviews.csv', 
                        model_max_length=384,
                        output_json_file_name='test.json',
                         sentence_transformer_name='all-MiniLM-L6-v2',
                        p_components=2,
                        # Keep use_labels=True always for KMeans+PCA (reason: there can be countless clusters without labels)                                   
                        use_labels=True):
     # Function that returns a new dataframe with reduced sentence sizes (as most bert models have a max_seq_length)
    data = updateDataFrame(input_file_name, model_max_length=model_max_length)
    print('Dataframe with reduced sentence sizes: \n')
    display(data)
    
    # Replacing all NaN fields under '2d_coor' column with an empty string
    print('Dataframe with NaN removed: \n')
    data['2d_coor'] = ''
    display(data)
    
    # Using a bert model from sentence_transformers to generate embeddings
    from sentence_transformers import SentenceTransformer
    model = SentenceTransformer(sentence_transformer_name)
    sentences = data['data_string']
    embeddings_for_kmeans = model.encode(sentences)
    
    # Reducing the dimensionality of embeddings with PCA After applying KMeans
    from sklearn.cluster import KMeans
    from sklearn.decomposition import PCA
    
    pca_2d_class = PCA(n_components=p_components).fit(embeddings_for_kmeans, list(data['data_category_number']) if use_labels else None)
    pca_2d = pca_2d_class.transform(embeddings_for_kmeans)
    
    kmeans = KMeans(n_clusters=len(data['data_category_number'].unique()))
    labels = kmeans.fit_predict(pca_2d, list(data['data_category_number']) if use_labels else None)
    labels_scale = kmeans.labels_

    data['2d_coor'] = pca_2d.tolist()
    display(data)
    
    new_labels = labels.tolist()
    list_of_points = []
    for idx in range(len(data['data_string'])):
        tmp_dict = {}
        tmp_dict["data_x"] = str(data['2d_coor'][idx][0])
        tmp_dict["data_y"] = str(data['2d_coor'][idx][1])
#         tmp_dict["data_category_number"] = str(data['data_category_number'][idx])
        tmp_dict["data_category_number"] = str(new_labels[idx])
        tmp_dict["data_id"] = str(data['data_id'][idx])

        tmp_dict["data_title"] = str(data['data_title'][idx])
        tmp_dict["data_category"] = str(data['data_category'][idx])

        list_of_points.append(tmp_dict)
        
    import json
    with open(output_json_file_name, "w") as outfile:
        json.dump(list_of_points, outfile)
        
    return data

In [ ]:
d = PCAAndKMeansWithCustomDataset(input_file_name='news_articles.csv', 
                        model_max_length=384,
                        output_json_file_name='news_articles_pcakmeans.json',
                         sentence_transformer_name='all-MiniLM-L6-v2',
                        p_components=2,
                        # Keep use_labels=True always for KMeans+PCA (reason: there can be countless clusters without labels)                                   
                        use_labels=True)